In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
from matplotlib import cm

n, c = (2, 10)
C = np.diag(c**(np.arange(n)/(n-1.)))
print(C)

f_sq = lambda x: x.T@C@x
f_hole = lambda x: 1.-np.exp(-x.T@C@x)

In [ ]:
%matplotlib notebook
%matplotlib notebook

def draw_f(x_path_sq = np.empty(0), fx_path_sq = np.empty(0), x_path_hole = np.empty(0), fx_path_hole = np.empty(0)):
    x = np.arange(-2, 2, 0.05)
    y = np.arange(-2, 2, 0.05)
    xv, yv = np.meshgrid(x, y, indexing='ij')
    zv_sq = np.zeros_like(xv)
    zv_hole = np.zeros_like(xv)
    for i in range(x.shape[0]):
        for j in range(y.shape[0]):
            zv_sq[i,j] = f_sq(np.array([xv[i,j], yv[i,j]]))
            zv_hole[i,j] = f_hole(np.array([xv[i,j], yv[i,j]]))
            
    fig = plt.figure(figsize=(8,8))
    ## f_sq
    ax1 = fig.add_subplot(221, projection="3d")
    surf = ax1.plot_surface(xv,yv,zv_sq,cmap=cm.coolwarm)
    if not x_path_sq.size == 0: ax1.plot(x_path_sq[:,0], x_path_sq[:,1], fx_path_sq, 'ko-')
    fig.colorbar(surf)
    ax1.set_xlabel('x')
    ax1.set_ylabel('y')
    ax1.set_zlabel('f')

    ax2 = fig.add_subplot(222)
    surf2 = plt.contourf(xv,yv,zv_sq,cmap=cm.coolwarm)
    if not x_path_sq.size == 0: ax2.plot(x_path_sq[:,0], x_path_sq[:,1], 'ko-')
    fig.colorbar(surf2)
    ax2.set_xlabel('x')
    ax2.set_ylabel('y')

    ## f_hole
    ax3 = fig.add_subplot(223, projection='3d')
    surf3 = ax3.plot_surface(xv,yv,zv_hole,cmap=cm.coolwarm)
    if not x_path_hole.size == 0: ax3.plot(x_path_hole[:,0], x_path_hole[:,1], fx_path_hole, 'ko-')
    fig.colorbar(surf3)
    ax3.set_xlabel('x')
    ax3.set_ylabel('y')
    ax3.set_zlabel('f')

    ax4 = fig.add_subplot(224)
    surf4 = plt.contourf(xv,yv,zv_hole,cmap=cm.coolwarm)
    if not x_path_hole.size == 0: ax4.plot(x_path_hole[:,0], x_path_hole[:,1], 'ko-')
    fig.colorbar(surf4)
    ax4.set_xlabel('x')
    ax4.set_ylabel('y')
    
    plt.show()
    

In [ ]:
draw_f()

In [ ]:
def gradDescentBacktraking(x, f, grad_f, C = np.eye(n)):
    alpha = 1
    fx = f(x)
    x_path = [x.copy()]
    fx_path = [fx.copy()]
    while True:
        grad_fx = grad_f(x)
        grad_fx = np.linalg.solve(C, grad_fx)
        delta = -grad_fx/np.linalg.norm(grad_fx)
        
        while f(x+alpha*delta) > fx + 0.5*grad_fx.T@(alpha*delta):
            alpha *= 0.5
            
        x += alpha*delta
        fx = f(x)
        
        x_path.append(x.copy())
        fx_path.append(fx.copy())
        
        alpha = min(1.2*alpha, np.inf)
        if np.linalg.norm(alpha*delta) < 1e-10:
            break
            
    
    return x, fx, np.stack(x_path), np.stack(fx_path)

grad_f_sq = lambda x: 2.*C@x
grad_f_hole = lambda x: 2.*np.exp(-x.T@C@x)*C@x

In [ ]:
n, c = (2, 10)
C = np.diag(c**(np.arange(n)/(n-1.)))

x_sq, fx_sq, x_path_sq, fx_path_sq = gradDescentBacktraking(1.5*np.ones(n), f_sq, grad_f_sq)
plt.figure()
plt.plot(fx_path_sq)
plt.grid()

x_hole, fx_hole, x_path_hole, fx_path_hole = gradDescentBacktraking(1.5*np.ones(n), f_hole, grad_f_hole)
plt.figure()
f2 = plt.plot(fx_path_hole)
plt.grid()

draw_f(x_path_sq, fx_path_sq, x_path_hole, fx_path_hole)

In [ ]:
x_sq, fx_sq, x_path_sq, fx_path_sq = gradDescentBacktraking(1.5*np.ones(n), f_sq, grad_f_sq, C)
plt.figure()
plt.plot(fx_path_sq)
plt.grid()

x_hole, fx_hole, x_path_hole, fx_path_hole = gradDescentBacktraking(1.5*np.ones(n), f_hole, grad_f_hole, C)
plt.figure()
f2 = plt.plot(fx_path_hole)
plt.grid()

draw_f(x_path_sq, fx_path_sq, x_path_hole, fx_path_hole)